# Perception CI Metrics Analysis

## 1. Data Loading and Configurations

In [ ]:
"""
Please make sure this notebook is ran using the "Python 2" kernel.
Please save notebooks with important results to your own folder in JupyterHub.

See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/blob/master/mined_metric/jupyter/README.md
"""
import json

import numpy as np

from mined_metric.jupyter.utils.data_access_util import *
from mined_metric.jupyter.utils.data_processing_util import *
from mined_metric.jupyter.utils.pcp_vis_util import *
from mined_metric.jupyter.utils.validation_vis_util import *

EXP_ID_CONTROL = "EXP_ID_CONTROL_PLACEHOLDER"
EXP_ID_CANDIDATE = "EXP_ID_CANDIDATE_PLACEHOLDER"
VALIDATION_ID = "VALIDATION_ID_PLACEHOLDER"

# Configuration files
CONFIG_PATH = "/mnt/sun-pcs01/jupyterhub/jhan/pcp_ci/pcp_ci_config.json"
RENDERER_DEFS_PATH = "/mnt/sun-pcs01/jupyterhub/jhan/pcp_ci/tracking_metrics_renderer_definitions.pbtxt"

In [ ]:
# Retrieve all data for both candidate and control branches
if "PLACEHOLDER" not in VALIDATION_ID:
    exp_data_control, exp_data_candidate = get_validation_data(VALIDATION_ID)
else:
    exp_data_control = get_experiment_data(EXP_ID_CONTROL)
    exp_data_candidate = get_experiment_data(EXP_ID_CANDIDATE)
print("Control Git SHA: {}".format(exp_data_control["experiment"]["gitsha"]))
print("Candidate Git SHA: {}".format(exp_data_candidate["experiment"]["gitsha"]))
print("Make sure the control and candidate Git SHAs are not swapped! (If they are, switch them.)")

In [ ]:
# Read configurations for metrics
with open(CONFIG_PATH) as f:
    configs = json.load(f)
configs_all = [c for section in configs.values() for c in section]

# Read configurations for Argus videos
with open("/mnt/sun-pcs01/jupyterhub/argus/argus_highlight_entities_layout.json") as f:
    argus_layout = json.load(f)

## 2. Data Summary

In [ ]:
# Calculate basic Chum URI summary statistics
chum_uris, meta_data_control, meta_data_candidate = parse_meta_data_for_validations(exp_data_control, exp_data_candidate)
stats = chum_summary_stats(chum_uris)
scenario_lookup = get_scenario_lookup(chum_uris)
print("Total number of Chum URIs: {}".format(len(chum_uris)))

In [ ]:
df = create_metric_aggregation_dataframe(configs_all, meta_data_control, meta_data_candidate)
plot_metric_aggregation_dataframe_as_one(df, skip_unchanged=True)
df

## 3. Metric Deviations

In [ ]:
# Calculate deviations in track metrics for all scenarios (takes about 3 minutes to run this cell)
track_metric_deviations = compare_track_metrics(meta_data_control, meta_data_candidate)

### 3.1 Recall - All Classes

In [ ]:
config = configs["all_crit_tight_recall"][0]
_, bins, bin_heights = vis_deviation_histogram(
    config["metric"],
    meta_data_control,
    meta_data_candidate,
    config["hist_num_bins"],
    config["hist_relative_deviation"],
    frequency = config["hist_frequency"],
    higher_is_better = config["higher_is_better"],
    skip_unchanged = config["hist_skip_unchanged"],
)
recall_all_bins = {config["metric"]: {"bins": bins, "bin_heights": bin_heights}}

In [ ]:
# Scenarios in a specific bar in the histogram of deviations in time to collision
bin_num = "lowest" # valid values are 1-9, "lowest", and "highest"
bin_largest_regression = get_histogram_bin_bounds(recall_all_bins, "all_crit_tight_recall", bin_num)
selected_chums_all = []
compare_select_scenarios(
    "all_crit_tight_recall",
    meta_data_control,
    meta_data_candidate,
    [],
    "rel_diff_between",
    scenario_lookup,
    deviation_range=bin_largest_regression,
    limit=3,
    argus_layout=argus_layout,
    selected_chums=selected_chums_all,
)

In [ ]:
# Introspect a single scenario
pcp_verification_introspection_mode(selected_chums_all, track_metric_deviations, scenario_lookup, argus_layout)

### 3.2 Recall - Bikes

In [ ]:
config = configs["bike_crit_tight_recall"][0]
_, bins, bin_heights = vis_deviation_histogram(
    config["metric"],
    meta_data_control,
    meta_data_candidate,
    config["hist_num_bins"],
    config["hist_relative_deviation"],
    frequency = config["hist_frequency"],
    higher_is_better = config["higher_is_better"],
    skip_unchanged = config["hist_skip_unchanged"],
)
recall_bikes_bins = {config["metric"]: {"bins": bins, "bin_heights": bin_heights}}

In [ ]:
# Scenarios in a specific bar in the histogram of deviations in time to collision
bin_num = "lowest" # valid values are 1-9, "lowest", and "highest"
bin_largest_regression = get_histogram_bin_bounds(recall_bikes_bins, "bike_crit_tight_recall", bin_num)
selected_chums_bikes = []
compare_select_scenarios(
    "bike_crit_tight_recall",
    meta_data_control,
    meta_data_candidate,
    [],
    "rel_diff_between",
    scenario_lookup,
    deviation_range=bin_largest_regression,
    limit=3,
    argus_layout=argus_layout,
    selected_chums=selected_chums_bikes,
)

In [ ]:
# Introspect a single scenario
pcp_verification_introspection_mode(selected_chums_bikes, track_metric_deviations, scenario_lookup, argus_layout)

### 3.3 Recall - Cars

In [ ]:
config = configs["car_crit_tight_recall"][0]
_, bins, bin_heights = vis_deviation_histogram(
    config["metric"],
    meta_data_control,
    meta_data_candidate,
    config["hist_num_bins"],
    config["hist_relative_deviation"],
    frequency = config["hist_frequency"],
    higher_is_better = config["higher_is_better"],
    skip_unchanged = config["hist_skip_unchanged"],
)
recall_cars_bins = {config["metric"]: {"bins": bins, "bin_heights": bin_heights}}

In [ ]:
# Scenarios in a specific bar in the histogram of deviations in time to collision
bin_num = "lowest" # valid values are 1-9, "lowest", and "highest"
bin_largest_regression = get_histogram_bin_bounds(recall_cars_bins, "car_crit_tight_recall", bin_num)
selected_chums_cars = []
compare_select_scenarios(
    "car_crit_tight_recall",
    meta_data_control,
    meta_data_candidate,
    [],
    "rel_diff_between",
    scenario_lookup,
    deviation_range=bin_largest_regression,
    limit=3,
    argus_layout=argus_layout,
    selected_chums=selected_chums_cars,
)

In [ ]:
# Introspect a single scenario
pcp_verification_introspection_mode(selected_chums_cars, track_metric_deviations, scenario_lookup, argus_layout)

### 3.4 Recall - Pedestrians

In [ ]:
config = configs["ped_crit_tight_recall"][0]
_, bins, bin_heights = vis_deviation_histogram(
    config["metric"],
    meta_data_control,
    meta_data_candidate,
    config["hist_num_bins"],
    config["hist_relative_deviation"],
    frequency = config["hist_frequency"],
    higher_is_better = config["higher_is_better"],
    skip_unchanged = config["hist_skip_unchanged"],
)
recall_peds_bins = {config["metric"]: {"bins": bins, "bin_heights": bin_heights}}

In [ ]:
# Scenarios in a specific bar in the histogram of deviations in time to collision
bin_num = "lowest" # valid values are 1-9, "lowest", and "highest"
bin_largest_regression = get_histogram_bin_bounds(recall_peds_bins, "ped_crit_tight_recall", bin_num)
selected_chums_peds = []
compare_select_scenarios(
    "ped_crit_tight_recall",
    meta_data_control,
    meta_data_candidate,
    [],
    "rel_diff_between",
    scenario_lookup,
    deviation_range=bin_largest_regression,
    limit=3,
    argus_layout=argus_layout,
    selected_chums=selected_chums_peds,
)

In [ ]:
# Introspect a single scenario
pcp_verification_introspection_mode(selected_chums_cars, track_metric_deviations, scenario_lookup, argus_layout)

## 4. Summary Tables

In [ ]:
pcp_ci_metrics = {
    "topline_mask_all_crit_tight_precision": {
        "metric_path": ["topline_mask", "all_crit_tight", "precision"],
        "renderer_def": "tracking::precision",
    },
    "topline_mask_all_crit_tight_recall": {
        "metric_path": ["topline_mask", "all_crit_tight", "recall"],
        "renderer_def": "tracking::recall",
    },
    "topline_mask_all_crit_tight_groundtruth_area": {
        "metric_path": ["topline_mask", "all_crit_tight", "groundtruth_area"],
    },
    "topline_mask_all_crit_tight_predicted_area": {
        "metric_path": ["topline_mask", "all_crit_tight", "predicted_area"],
    },
    "topline_mask_all_crit_tight_false_positive_area": {
        "metric_path": ["topline_mask", "all_crit_tight", "false_positive_area"],
    },
    "topline_mask_all_crit_tight_false_negative_area": {
        "metric_path": ["topline_mask", "all_crit_tight", "false_negative_area"],
    },
}

filtered_data_control = filter_pcp_ci_meta_data(meta_data_control, pcp_ci_metrics)
filtered_data_candidate = filter_pcp_ci_meta_data(meta_data_candidate, pcp_ci_metrics)

In [ ]:
df_agg_metrics = parse_aggregate_data_for_validations(exp_data_control, exp_data_candidate)
df_agg_summary = create_pcp_ci_summary_table(df_agg_metrics, pcp_ci_metrics, RENDERER_DEFS_PATH)
vis_pcp_ci_summary_table(df_agg_summary)

In [ ]:
options = pcp_ci_metrics.keys()
metric_selector = Dropdown(
    options=options,
    description='Metric:',
    layout=Layout(width='max-content'),
)

def update(metric):
    bins = vis_deviation_histogram(
        metric_key=metric,
        meta_data_control=filtered_data_control,
        meta_data_candidate=filtered_data_candidate,
        num_bins=9,
        relative_deviation=False,
        frequency=False,
    )

In [ ]:
func = interact(update, metric=metric_selector)

## 5. Additional Metrics

In [ ]:
pcp_ci_agg_metrics = {
    "Yaw Error at High Velocity": {
        "metric_path": ["all_objects,class:car", "scalars", "geometry::yawErrorAtHighVel::mean"],
        "higher_is_better": False,
    },
    "Yaw Error at Low Velocity": {
        "metric_path": ["all_objects,class:car", "scalars", "geometry::yawErrorAtLowVel::mean"],
        "higher_is_better": False,
    },
    "Yaw Error Ignore Heading at High Velocity": {
        "metric_path": ["all_objects,class:car", "scalars", "geometry::yawErrorIgnoreHeadingAtHighVel::mean"],
        "higher_is_better": False,
    },
    "Yaw Error Ignore Heading at Low Velocity": {
        "metric_path": ["all_objects,class:car", "scalars", "geometry::yawErrorIgnoreHeadingAtLowVel::mean"],
        "higher_is_better": False,
    },
}

agg_metrics_control = get_pcp_ci_agg_metrics(EXP_ID_CONTROL)
agg_metrics_candidate = get_pcp_ci_agg_metrics(EXP_ID_CANDIDATE)
filtered_agg_metrics_control = filter_pcp_ci_agg_metrics(agg_metrics_control, pcp_ci_agg_metrics)
filtered_agg_metrics_candidate = filter_pcp_ci_agg_metrics(agg_metrics_candidate, pcp_ci_agg_metrics)
create_pcp_ci_agg_metrics_table(pcp_ci_agg_metrics, filtered_agg_metrics_control, filtered_agg_metrics_candidate)